In [23]:
# -*- coding: utf-8 -*-
"""
@author: radoslaw guzinski
Copyright: (C) 2017, Radoslaw Guzinski
"""
import os
import time

from osgeo import gdal

import pyDMS.pyDMSUtils as utils
from pyDMS.pyDMS import DecisionTreeSharpener, NeuralNetworkSharpener
from pyDMS.pyDMS import REG_sknn_ann, REG_sklearn_ann

highResFilename = r"F:\Suzan\Quality_Assessment\New_folder_DS\Downscaling\Data\Data_MWEA\NDVI_out\2215.tif"
lowResFilename = r"F:\Suzan\Quality_Assessment\New_folder_DS\Downscaling\Data\Data_MWEA\WAPOR.v2_dekadal_L2_AETI_D\2215.tif"
outputFilename = r"F:\Suzan\Quality_Assessment\New_folder_DS\Downscaling\Data\Data_MWEA\Results\New\2215.tif"

In [24]:
if __name__ == "__main__":

    useDecisionTree = True

    commonOpts = {"highResFiles":               [highResFilename],
                  "lowResFiles":               [lowResFilename],
                  "lowResGoodQualityFlags":     [0],      #{0} , 255
                  "cvHomogeneityThreshold":     0.25,    #{0.25} , 0
                  "movingWindowSize":           150,     #{150} , 15 
                  "disaggregatingTemperature":  False}       #{False} , True
    dtOpts =     {"perLeafLinearRegression":    True,  
                  "linearRegressionExtrapolationRatio": 0.25}
    sknnOpts =   {'hidden_layer_sizes':         (10,),
                  'activation':                 'tanh'}
    nnOpts =     {"regressionType":             REG_sklearn_ann,
                  "regressorOpt":               sknnOpts}

    start_time = time.time()

    if useDecisionTree:
        opts = commonOpts.copy()
        opts.update(dtOpts)
        disaggregator = DecisionTreeSharpener(**opts)
    else:
        opts = commonOpts.copy()
        opts.update(nnOpts)
        disaggregator = NeuralNetworkSharpener(**opts)

    print("Training regressor...")
    disaggregator.trainSharpener()
    print("Sharpening...")
    downscaledFile = disaggregator.applySharpener(highResFilename, lowResFilename)
    print("Residual analysis...")
    residualImage, correctedImage = disaggregator.residualAnalysis(downscaledFile, lowResFilename,
                                                                   doCorrection=True)
    print("Saving output...")
    highResFile = gdal.Open(highResFilename)
    if correctedImage is not None:
        outImage = correctedImage
    else:
        outImage = downscaledFile
    # outData = utils.binomialSmoother(outData)
    outFile = utils.saveImg(outImage.GetRasterBand(1).ReadAsArray(),
                            outImage.GetGeoTransform(),
                            outImage.GetProjection(),
                            outputFilename)
    residualFile = utils.saveImg(residualImage.GetRasterBand(1).ReadAsArray(),
                                 residualImage.GetGeoTransform(),
                                 residualImage.GetProjection(),
                                 os.path.splitext(outputFilename)[0] + "_residual" +
                                 os.path.splitext(outputFilename)[1])

    outFile = None
    residualFile = None
    downsaceldFile = None
    highResFile = None

    print(time.time() - start_time, "seconds")


Training regressor...
Number of training elements for is 9685 representing 62% of avaiable low-resolution data.
Number of training elements for is 2345 representing 62% of avaiable low-resolution data.
Number of training elements for is 1343 representing 48% of avaiable low-resolution data.
Number of training elements for is 272 representing 35% of avaiable low-resolution data.
Number of training elements for is 9685 representing 62% of avaiable low-resolution data.
Sharpening...
Saved MEM
Saved MEM
Saved MEM
Saved MEM
Saved MEM
Residual analysis...
Saved MEM
Saved MEM
Saved MEM
LR residual bias: -0.025720490096383095
LR residual RMSD: 0.3041344602842667
Saving output...
Saved F:\Suzan\Quality_Assessment\New_folder_DS\Downscaling\Data\Data_MWEA\Results\New\2215.tif
Saved F:\Suzan\Quality_Assessment\New_folder_DS\Downscaling\Data\Data_MWEA\Results\New\2215_residual.tif
18.307399034500122 seconds
